## Katrin Rylander
#### Uppgift 2 - EDA av API
#### Explorativ undersökning av följande enpoints:
- v1/cryptocurrency/quotes/latest
- v1/cryptocurrency/listings/latest

**CoinMarketCap ID Map**
#### I take one step back to check what currencies are available and how they are identified

In [1]:
from requests import Session
from requests.exceptions import ConnectionError, Timeout, TooManyRedirects
import json
from dotenv import load_dotenv
import os
from pprint import pprint

load_dotenv()

API_KEY = os.getenv("COINMARKET_API")

url_map = "https://pro-api.coinmarketcap.com/v1/cryptocurrency/map"

headers = {
    "Accepts": "application/json",
    "X-CMC_PRO_API_KEY": API_KEY,
}


session = Session()
session.headers.update(headers)

try:
  response = session.get(url=url_map)
  data = json.loads(response.text)
except (ConnectionError, Timeout, TooManyRedirects) as e:
  print(e)

pprint(data)

{'data': [{'first_historical_data': '2010-07-13T00:05:00.000Z',
           'id': 1,
           'is_active': 1,
           'last_historical_data': '2025-02-13T11:05:00.000Z',
           'name': 'Bitcoin',
           'platform': None,
           'rank': 1,
           'slug': 'bitcoin',
           'status': 1,
           'symbol': 'BTC'},
          {'first_historical_data': '2013-04-28T18:45:00.000Z',
           'id': 2,
           'is_active': 1,
           'last_historical_data': '2025-02-13T11:05:00.000Z',
           'name': 'Litecoin',
           'platform': None,
           'rank': 16,
           'slug': 'litecoin',
           'status': 1,
           'symbol': 'LTC'},
          {'first_historical_data': '2013-04-28T18:45:00.000Z',
           'id': 3,
           'is_active': 1,
           'last_historical_data': '2025-02-13T11:05:00.000Z',
           'name': 'Namecoin',
           'platform': None,
           'rank': 963,
           'slug': 'namecoin',
           'status': 1,
        

In [22]:
import pandas as pd

# Convert to DataFrame
df = pd.DataFrame(data["data"])

In [24]:
df.head()

id  rank       name symbol       slug  is_active  status  \
0   1     1    Bitcoin    BTC    bitcoin          1       1   
1   2    18   Litecoin    LTC   litecoin          1       1   
2   3   958   Namecoin    NMC   namecoin          1       1   
3   4  5637  Terracoin    TRC  terracoin          1       1   
4   5  1025   Peercoin    PPC   peercoin          1       1   

      first_historical_data      last_historical_data platform  
0  2010-07-13T00:05:00.000Z  2025-02-12T12:55:00.000Z     None  
1  2013-04-28T18:45:00.000Z  2025-02-12T12:55:00.000Z     None  
2  2013-04-28T18:45:00.000Z  2025-02-12T12:55:00.000Z     None  
3  2013-04-28T18:45:00.000Z  2025-02-12T12:55:00.000Z     None  
4  2013-04-28T18:45:00.000Z  2025-02-12T12:55:00.000Z     None

In [25]:
df_sorted = df.sort_values(by="rank", ascending=True)
df_sorted.head(10)

id  rank         name symbol      slug  is_active  status  \
0       1     1      Bitcoin    BTC   bitcoin          1       1   
117  1027     2     Ethereum    ETH  ethereum          1       1   
97    825     3  Tether USDt   USDT    tether          1       1   
19     52     4          XRP    XRP       xrp          1       1   
977  5426     5       Solana    SOL    solana          1       1   
282  1839     6          BNB    BNB       bnb          1       1   
617  3408     7         USDC   USDC  usd-coin          1       1   
25     74     8     Dogecoin   DOGE  dogecoin          1       1   
324  2010     9      Cardano    ADA   cardano          1       1   
309  1958    10         TRON    TRX      tron          1       1   

        first_historical_data      last_historical_data  \
0    2010-07-13T00:05:00.000Z  2025-02-12T12:55:00.000Z   
117  2015-08-07T14:45:00.000Z  2025-02-12T12:55:00.000Z   
97   2015-02-25T13:30:00.000Z  2025-02-12T12:55:00.000Z   
19   2013-08-04T18:50:00.000Z  2025-02-12T12:55:00.000Z   
977  2020-04-10T04:55:00.000Z  2025-02-12T12:55:00.000Z   
282  2017-07-25T04:30:00.000Z  2025-02-12T12:55:00.000Z   
617  2018-10-08T18:45:00.000Z  2025-02-12T12:55:00.000Z   
25   2013-12-15T14:40:00.000Z  2025-02-12T12:55:00.000Z   
324  2017-10-01T20:30:00.000Z  2025-02-12T12:55:00.000Z   
309  2017-09-13T01:15:00.000Z  2025-02-12T12:55:00.000Z   

                                              platform  
0                                                 None  
117                                               None  
97   {'id': 1, 'name': 'Ethereum', 'symbol': 'ETH',...  
19                                                None  
977                                               None  
282                                               None  
617  {'id': 1, 'name': 'Ethereum', 'symbol': 'ETH',...  
25                                                None  
324                                               None  
309                                               None

#### NOTE: it might be best to choose 2 cryptocurrencies ranked in top 10, to make sure the price changes often.
#### Interesting choices: 
- XRP (one person in our team trades it and finds getting more metrics on this currency useful) 
- TRON - because it of its interesting applications: designed to make digital content sharing cheaper and faster

**v1/cryptocurrency/quotes/latest**
#### NOTE from CoinMarketCap: 
- Per our Best Practices we recommend utilizing CMC ID instead of cryptocurrency symbols to securely identify cryptocurrencies with our other endpoints and in your own application logic.

In [13]:
from requests import Session
from requests.exceptions import ConnectionError, Timeout, TooManyRedirects
import json
from dotenv import load_dotenv
import os
import time  # To add a delay between API calls 

load_dotenv()

# API Configuration
API_KEY = os.getenv("COINMARKET_API")
API_URL = 'https://pro-api.coinmarketcap.com/v1/cryptocurrency/quotes/latest' 
CMC_ID  = 52 # id that corresponds to XRP

FIAT_CURRENCIES = ["SEK", "NOK", "DKK", "EUR"]  # List of currencies to fetch

# Request headers
headers = {
    'Accepts': 'application/json',
    'X-CMC_PRO_API_KEY': API_KEY,
  }


# Function to fetch cryptocurrency data from API
def fetch_crypto_data(crypto_id, currencies):
    all_data = {}

    for currency in currencies:
        parameters = {"id": crypto_id, "convert": currency}  # Using ID instead of symbol
        # Fetch data from API
        session = Session()
        session.headers.update(headers)
        try:
          response = session.get(url, params=parameters)
          data = json.loads(response.text)
        except (ConnectionError, Timeout, TooManyRedirects) as e:
          print(e)

        if "data" in data and str(crypto_id) in data["data"]:
            all_data[currency] = data["data"][str(crypto_id)]
        else:
            print(f"Error fetching data for CMC ID {crypto_id} in {currency}.")
        
        # Optional: Add a short delay to prevent hitting API limits
        time.sleep(1)

    return all_data

# Step 1: Fetch all cryptocurrency data
crypto_raw_data = fetch_crypto_data(CMC_ID, FIAT_CURRENCIES)



In [16]:
crypto_raw_data['SEK']

{'id': 52,
 'name': 'XRP',
 'symbol': 'XRP',
 'slug': 'xrp',
 'num_market_pairs': 1529,
 'date_added': '2013-08-04T00:00:00.000Z',
 'tags': ['medium-of-exchange',
  'enterprise-solutions',
  'xrp-ecosystem',
  'arrington-xrp-capital-portfolio',
  'galaxy-digital-portfolio',
  'a16z-portfolio',
  'pantera-capital-portfolio',
  'ftx-bankruptcy-estate',
  '2017-2018-alt-season',
  'klaytn-ecosystem',
  'made-in-america'],
 'max_supply': 100000000000,
 'circulating_supply': 57762545657,
 'total_supply': 99986504676,
 'is_active': 1,
 'infinite_supply': False,
 'platform': None,
 'cmc_rank': 4,
 'is_fiat': 0,
 'self_reported_circulating_supply': None,
 'self_reported_market_cap': None,
 'tvl_ratio': None,
 'last_updated': '2025-02-13T14:14:00.000Z',
 'quote': {'SEK': {'price': 26.414380219248034,
   'volume_24h': 48260558497.859085,
   'volume_change_24h': -16.1466,
   'percent_change_1h': 0.01406113,
   'percent_change_24h': 2.50593394,
   'percent_change_7d': 1.24363631,
   'percent_chang

In [20]:
crypto_raw_data['NOK']

{'id': 52,
 'name': 'XRP',
 'symbol': 'XRP',
 'slug': 'xrp',
 'num_market_pairs': 1529,
 'date_added': '2013-08-04T00:00:00.000Z',
 'tags': ['medium-of-exchange',
  'enterprise-solutions',
  'xrp-ecosystem',
  'arrington-xrp-capital-portfolio',
  'galaxy-digital-portfolio',
  'a16z-portfolio',
  'pantera-capital-portfolio',
  'ftx-bankruptcy-estate',
  '2017-2018-alt-season',
  'klaytn-ecosystem',
  'made-in-america'],
 'max_supply': 100000000000,
 'circulating_supply': 57762545657,
 'total_supply': 99986504676,
 'is_active': 1,
 'infinite_supply': False,
 'platform': None,
 'cmc_rank': 4,
 'is_fiat': 0,
 'self_reported_circulating_supply': None,
 'self_reported_market_cap': None,
 'tvl_ratio': None,
 'last_updated': '2025-02-13T14:14:00.000Z',
 'quote': {'NOK': {'price': 27.46510993267366,
   'volume_24h': 50180300788.96402,
   'volume_change_24h': -16.1466,
   'percent_change_1h': 0.01406113,
   'percent_change_24h': 2.50593394,
   'percent_change_7d': 1.24363631,
   'percent_change_

In [17]:
# Function to extract metrics from API response
def extract_crypto_metrics(crypto_data):
    crypto_metrics = {
        "Rank": None,
        "Name": None,
        "Symbol": None,
        "Circulating Supply": None,
        "Total Supply": None,
        "Max Supply": None,
        "Dominance (%)": None,
        "24h % Change": None,
        "7d % Change": None,
        "30d % Change": None,
    }

    for currency, coin in crypto_data.items():
        quote = coin["quote"][currency]

        # Assign general crypto data (only once)
        if crypto_metrics["Rank"] is None:
            crypto_metrics["Rank"] = coin["cmc_rank"]
            crypto_metrics["Name"] = coin["name"]
            crypto_metrics["Symbol"] = coin["symbol"]
            crypto_metrics["Circulating Supply"] = round(coin["circulating_supply"], 2)
            crypto_metrics["Total Supply"] = round(coin["total_supply"], 2) if coin["total_supply"] else "N/A"
            crypto_metrics["Max Supply"] = round(coin["max_supply"], 2) if coin["max_supply"] else "Unlimited"
            #crypto_metrics["Dominance (%)"] = round(coin["quote"]["USD"]["market_cap_dominance"], 2)
            #crypto_metrics["24h % Change"] = round(coin["quote"]["USD"]["percent_change_24h"], 2)
            #crypto_metrics["7d % Change"] = round(coin["quote"]["USD"]["percent_change_7d"], 2)
            #crypto_metrics["30d % Change"] = round(coin["quote"]["USD"]["percent_change_30d"], 2)

        # Store currency-specific data
        crypto_metrics[f"Price ({currency})"] = round(quote["price"], 4)
        crypto_metrics[f"Market Cap ({currency})"] = round(quote["market_cap"], 2)
        crypto_metrics[f"Fully Diluted Market Cap ({currency})"] = round(quote["fully_diluted_market_cap"], 2)
        crypto_metrics[f"24h Volume ({currency})"] = round(quote["volume_24h"], 2)
        crypto_metrics[f"Volume/Market Cap Ratio ({currency})"] = round(quote["volume_24h"] / quote["market_cap"], 4)
        crypto_metrics[f"Liquidity Score ({currency}) (%)"] = round(quote["volume_24h"] / quote["market_cap"] * 100, 2)
        crypto_metrics[f"All-Time High ({currency})"] = round(quote["price"] / (1 - quote["percent_change_24h"] / 100), 4)

    return crypto_metrics

# Step 2: Extract relevant metrics
crypto_metrics = extract_crypto_metrics(crypto_raw_data)

In [24]:
len(crypto_metrics)

38

In [19]:
import pandas as pd

# Convert extracted metrics into a DataFrame
crypto_df = pd.DataFrame([crypto_metrics])

crypto_df

Rank Name Symbol  Circulating Supply  Total Supply    Max Supply  \
0     4  XRP    XRP         57762545657   99986504676  100000000000   

  Dominance (%) 24h % Change 7d % Change 30d % Change  ...  \
0          None         None        None         None  ...   

   Volume/Market Cap Ratio (DKK)  Liquidity Score (DKK) (%)  \
0                         0.0316                       3.16   

   All-Time High (DKK)  Price (EUR)  Market Cap (EUR)  \
0                17.95       2.3463      1.355309e+11   

   Fully Diluted Market Cap (EUR)  24h Volume (EUR)  \
0                    2.346346e+11      4.286906e+09   

   Volume/Market Cap Ratio (EUR)  Liquidity Score (EUR) (%)  \
0                         0.0316                       3.16   

   All-Time High (EUR)  
0               2.4067  

[1 rows x 38 columns]

**v1/cryptocurrency/listings/latest**

In [2]:
import requests
import pandas as pd
import json
from dotenv import load_dotenv
import os

load_dotenv()

API_KEY = os.getenv("COINMARKET_API")

URL = "https://pro-api.coinmarketcap.com/v1/cryptocurrency/listings/latest"

# Define headers for authentication
headers = {
    "Accepts": "application/json",
    "X-CMC_PRO_API_KEY": API_KEY,
}

# Define parameters (limit to top 10 for this example)
params = {
    "start": 1,  # Rank starting from 1
    "limit": 10,  # Get top 10 cryptocurrencies
    "convert": "SEK"  # Convert prices to SEK
}

# Fetch data from CoinMarketCap
response = requests.get(URL, headers=headers, params=params)
data = response.json()


#### This code gathers key cryptocurrency metrics in SEK (Swedish Krona) from the CoinMarketCap API and stores them in a list. Below is a breakdown of each metric:

- Basic Information:
    - Rank → The cryptocurrency’s ranking based on market cap.
    - Name → The full name of the cryptocurrency (e.g., Bitcoin, Ethereum).
    - Symbol → The short trading symbol (e.g., BTC, ETH).
- 💰 Price & Market Metrics:
    - Price (SEK) → The latest price of the cryptocurrency in SEK.
    - Market Cap (SEK) → The total value of all circulating coins (price × circulating supply).
    - Fully Diluted Market Cap (SEK) → The estimated total value if all coins were in circulation.
- 📈 Trading Volume & Liquidity:
    - 24h Volume (SEK) → The total amount traded in the last 24 hours.
    - Volume/Market Cap Ratio → A measure of liquidity; higher values suggest more active trading.
    - Liquidity Score (%) → Volume/Market Cap Ratio multiplied by 100 to show liquidity in percentage.
- 🔄 Supply Metrics:
    - Circulating Supply → The number of coins currently available for trading.
    - Total Supply → The total number of coins that exist (if available).
    - Max Supply → The maximum number of coins that will ever exist (if defined, otherwise "Unlimited").
- 📊 Market Influence & Performance:
    - Dominance (%) → How much of the total crypto market cap this coin represents.
    - 24h % Change → Price change in the last 24 hours.
    - 7d % Change → Price change over the past 7 days.
    - 30d % Change → Price change over the past 30 days.
    - All-Time High (SEK) → An estimate of the highest price the coin has ever reached.

In [3]:
# Extract useful metrics
crypto_list = []
for coin in data["data"]:
    quote = coin["quote"]["SEK"]
    crypto_list.append({
        #  Basic Information: The cryptocurrency’s ranking based on market cap.
        "Rank": coin["cmc_rank"],
        # Basic Information: The full name of the cryptocurrency (e.g., Bitcoin, Ethereum).
        "Name": coin["name"],
        # Basic Information: The short trading symbol (e.g., BTC, ETH).
        "Symbol": coin["symbol"],
        # Price & Market Metrics: The latest price of the cryptocurrency in SEK.
        "Price (SEK)": round(quote["price"], 4),
        # Price & Market Metrics: The total value of all circulating coins (price × circulating supply).
        "Market Cap (SEK)": round(quote["market_cap"], 2),
        # Price & Market Metrics: The total value of all circulating coins (price × circulating supply).
        "Fully Diluted Market Cap (SEK)": round(quote["fully_diluted_market_cap"], 2),
        # Trading Volume & Liquidity: 24h Volume (SEK) → The total amount traded in the last 24 hours.
        "24h Volume (SEK)": round(quote["volume_24h"], 2),
        # Trading Volume & Liquidity:
        "Volume/Market Cap Ratio": round(quote["volume_24h"] / quote["market_cap"], 4),
        # Trading Volume & Liquidity:
        "Liquidity Score (%)": round(quote["volume_24h"] / quote["market_cap"] * 100, 2),
        # Supply Metrics: Circulating Supply → The number of coins currently available for trading.
        "Circulating Supply": round(coin["circulating_supply"], 2),
        # Supply Metrics: Total Supply → The total number of coins that exist (if available).
        "Total Supply": round(coin["total_supply"], 2) if coin["total_supply"] else "N/A",
        # Supply Metrics: Max Supply → The maximum number of coins that will ever exist (if defined, otherwise "Unlimited").
        "Max Supply": round(coin["max_supply"], 2) if coin["max_supply"] else "Unlimited",
        # Market Influence & Performance: Dominance (%) → How much of the total crypto market cap this coin represents.
        "Dominance (%)": round(quote["market_cap_dominance"], 2),
        # Market Influence & Performance: 24h % Change → Price change in the last 24 hours.
        "24h % Change": round(quote["percent_change_24h"], 2),
        # Market Influence & Performance: 7d % Change → Price change over the past 7 days.
        "7d % Change": round(quote["percent_change_7d"], 2),
        # Market Influence & Performance: 30d % Change → Price change over the past 30 days.
        "30d % Change": round(quote["percent_change_30d"], 2),
        # Market Influence & Performance: All-Time High (SEK) → An estimate of the highest price the coin has ever reached.
        "All-Time High (SEK)": round(quote["price"] / (1 - quote["percent_change_24h"] / 100), 4)
    })
    

In [4]:
# Convert to a Pandas DataFrame
df_top10 = pd.DataFrame(crypto_list)

# Display the DataFrame
df_top10


Rank         Name Symbol   Price (SEK)  Market Cap (SEK)  \
0     1      Bitcoin    BTC  1.043162e+06      2.067928e+13   
1     2     Ethereum    ETH  2.896338e+04      3.491403e+12   
2     3  Tether USDt   USDT  1.086460e+01      1.541961e+12   
3     4          XRP    XRP  2.661570e+01      1.537393e+12   
4     5          BNB    BNB  7.660807e+03      1.091504e+12   
5     6       Solana    SOL  2.085744e+03      1.018199e+12   
6     7         USDC   USDC  1.086400e+01      6.093166e+11   
7     8     Dogecoin   DOGE  2.791900e+00      4.132775e+11   
8     9      Cardano    ADA  8.535300e+00      3.004198e+11   
9    10         TRON    TRX  2.565700e+00      2.209065e+11   

   Fully Diluted Market Cap (SEK)  24h Volume (SEK)  Volume/Market Cap Ratio  \
0                    2.190641e+13      5.568452e+11                   0.0269   
1                    3.491403e+12      2.841356e+11                   0.0814   
2                    1.559795e+12      1.169072e+12                   0.7582   
3                    2.661574e+12      5.952382e+10                   0.0387   
4                    1.091504e+12      4.151841e+10                   0.0380   
5                    1.238776e+12      4.656251e+10                   0.0457   
6                    6.093166e+11      1.055483e+11                   0.1732   
7                    4.132775e+11      2.253482e+10                   0.0545   
8                    3.840900e+11      1.193183e+10                   0.0397   
9                    2.209065e+11      7.537030e+09                   0.0341   

   Liquidity Score (%)  Circulating Supply  Total Supply    Max Supply  \
0                 2.69        1.982365e+07  1.982365e+07      21000000   
1                 8.14        1.205454e+08  1.205454e+08     Unlimited   
2                75.82        1.419253e+11  1.435668e+11     Unlimited   
3                 3.87        5.776255e+10  9.998650e+10  100000000000   
4                 3.80        1.424790e+08  1.424790e+08     Unlimited   
5                 4.57        4.881708e+08  5.939250e+08     Unlimited   
6                17.32        5.608584e+10  5.608584e+10     Unlimited   
7                 5.45        1.480282e+11  1.480282e+11     Unlimited   
8                 3.97        3.519720e+10  4.499508e+10   45000000000   
9                 3.41        8.609999e+10  8.610000e+10     Unlimited   

   Dominance (%)  24h % Change  7d % Change  30d % Change  All-Time High (SEK)  
0          59.96         -0.17        -2.44         -0.10         1.041401e+06  
1          10.13          1.38        -4.12        -16.40         2.936745e+04  
2           4.47          0.01        -0.03          0.06         1.086580e+01  
3           4.46          0.74         1.47         -4.26         2.681410e+01  
4           3.17          9.20        21.57          1.87         8.436994e+03  
5           2.95         -2.66        -3.46          2.86         2.031776e+03  
6           1.77          0.01         0.00          0.01         1.086510e+01  
7           1.20         -0.32        -1.38        -25.97         2.782900e+00  
8           0.87         -1.11         5.28        -18.20         8.441700e+00  
9           0.64         -3.12         2.13          5.49         2.488100e+00

In [5]:
# Save to CSV (optional)
df_top10.to_csv("crypto_data_top10.csv", index=False)
print("Data saved to crypto_data.csv ✅")

Data saved to crypto_data.csv ✅
